# Dash Board of Economy Estimation

## Required Packages

In [1]:
import random
import numpy as np
import pandas as pd
import plotly.express as px
from tqdm.auto import tqdm

## Parameters Setup

In [2]:
Population = 100
Round = 4000
Incomes = [1.1, -1.0]

In [3]:
def gini(vec):
    a = sorted(vec)

    n = len(a)

    triu = np.triu(np.ones(n), k=0)
    b = np.matmul(a, triu)

    b = np.insert(b, 0, 0)

    if b[-1] == 0:
        return

    g = np.sum(b) / (len(b) * b[-1] / 2)

    if g > 1 or g < 0:
        return

    return g


vec = [1, 2, 1]
gini(vec)

0.875

## Estimation

In [4]:
mat = [np.zeros(Population)]
mat2 = [np.zeros(Population)]

for r in tqdm(range(Round)):
    vec = np.array([random.choice(Incomes) for _ in range(Population)])

    mat.append(mat[-1] + vec)

    latest = mat2[-1] + vec
    if np.mean(latest) > 0:
        #         latest = latest - (np.mean(latest) + 2 * np.std(latest))
        lstest = latest - sorted(latest)[int(Population / 4 * 3)]
        latest[latest < 0] = 0
        #         latest = latest * 0.01
        #         if np.sum(latest) > np.sum(vec):
        #             latest /= (np.sum(latest) * np.sum(vec))
        mat2.append(mat2[-1] + vec + latest * 0.001)
    else:
        mat2.append(latest)

mat = np.array(mat)
mat2 = np.array(mat2)

  0%|          | 0/4000 [00:00<?, ?it/s]

## Plots

In [5]:
def plot(df):
    title = 'Gini'
    gs = [gini(df.iloc[e].values) for e in tqdm(range(len(df)))]
    fig = px.line(gs, title=title)
    fig.show()

    title = 'Trace'
    fig = px.line(df.iloc[range(0, len(df), int(len(df)/100))], title=title)
    fig.show()
    
    title = 'Histogram of Last'
    fig = px.histogram(df.iloc[[int(len(df)/2), len(df)-1]].transpose(), nbins=100, title=title)
    fig.show()
    
    return fig
    
    title = 'Distributions'
    fig = px.box(df.iloc[range(0, len(df), int(len(df)/10))].transpose(), title=title)
    fig.show()

    k = int(Round/5)
    orders = df.iloc[k].argsort()
    head = [int(e) for e in orders.iloc[-10:].values]
    tail = [int(e) for e in orders.iloc[:10].values]

    _df = df.iloc[range(0, len(df), int(len(df)/100))]

    title = f'Fate [{k}]'
    fig = px.line(_df, y=head + tail, title=title)

    for j, d in enumerate(fig.data):
        name = int(d['name'])

        if name in head:
            color = 'red'
        else:
            color = 'black'

        d['line']['color'] = color

    fig.show()

    k = int(Round/2)
    orders = df.iloc[k].argsort()
    head = [int(e) for e in orders.iloc[-10:].values]
    tail = [int(e) for e in orders.iloc[:10].values]

    _df = df.iloc[range(0, len(df), int(len(df)/100))]

    title = f'Fate [{k}]'
    fig = px.line(_df, y=head + tail, title=title)

    for j, d in enumerate(fig.data):
        name = int(d['name'])

        if name in head:
            color = 'red'
        else:
            color = 'black'

        d['line']['color'] = color

    fig.show()
    

In [6]:
df = pd.DataFrame(mat)
fig = plot(df)

  0%|          | 0/4001 [00:00<?, ?it/s]

In [14]:
fig

In [13]:
fig.data[1]['marker']['opacity'] = 0.2

In [7]:
df = pd.DataFrame(mat2)
plot(df)

  0%|          | 0/4001 [00:00<?, ?it/s]